In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
cd D:\nvb\GODS_NG\KB-InfoBot

D:\nvb\GODS_NG\KB-InfoBot


In [3]:
from deep_dialog.dialog_system import MovieDict, DictReader, Database
from deep_dialog.objects import SlotReader
from deep_dialog.agents.agent_simpleRL_allact_torch import AgentSimpleRLAllAct
from deep_dialog.usersims import RuleSimulator
from deep_dialog.usersims.template_nlg import TemplateNLG
from deep_dialog.usersims.s2s_nlg import S2SNLG
from deep_dialog.dialog_system.dialog_manager import DialogManager

In [4]:
params = {}
params['act_set'] = r'D:\nvb\GODS_NG\KB-InfoBot\data\dia_acts.txt'
params['dataset'] = 'imdb_S'


params['template_path'] = r'D:\nvb\GODS_NG\KB-InfoBot\data\templates_p3.pkl'
params['nlg_slots_path'] = r'D:\nvb\GODS_NG\KB-InfoBot\data\nlg_slot_set.txt'
params['nlg_temp'] = 1
params['nlg_model_path'] = r'D:\nvb\GODS_NG\KB-InfoBot\data\pretrained\lstm_tanh_[1470015675.73]_115_120_0.657_p3.pkl'
# params['template_path'] = r'D:\nvb\GODS_NG\KB-InfoBot\data\templates.j'


params['max_req'] = 1 # только при SL
params['frac'] = 0.5 # только при SL
params['upd'] = .05 # C
params['input'] = 'entropy' 
params['pol_start'] = 10
params['nhid'] = 50
params['lr'] = 0.005
params['batch'] = 128
params['ment'] = 0 # RLLoss
params['ts'] = 0.5 # только при SL
params['tr'] = 5 # только при SL

params['model_name'] = '03_06_soft_rl_torch_v3_ent.m'


max_turn = 20
err_prob = .5
dk_prob = .5
sub_prob = .05
nlg_temp = 1
max_first_turn = 5


slot_path = r'D:\nvb\GODS_NG\KB-InfoBot\data\imdb-S\slot_set.txt'
dict_path = r'D:\nvb\GODS_NG\KB-InfoBot/data/imdb-S/dicts_.json'
db_full_path = r'D:\nvb\GODS_NG\KB-InfoBot\data\imdb-S\db.txt'
db_inc_path = r'D:\nvb\GODS_NG\KB-InfoBot\data\imdb-S\incomplete_db_0.20.txt'

In [5]:
act_set = DictReader()
act_set.load_dict_from_file(params['act_set'])

In [6]:
slot_set = SlotReader(slot_path)

In [7]:
movie_kb = MovieDict(dict_path)

In [8]:
db_full = Database(db_full_path, movie_kb, name=params['dataset'])
db_inc = Database(db_inc_path, movie_kb, name='incomplete_db_0.20')

In [9]:
# params['template_path'] = r'F:\nvb\KB-InfoBot\data\templates_p3.pkl'
# nlg = S2SNLG(params['template_path'], params['nlg_slots_path'], params['nlg_model_path'], 
#         params['nlg_temp'])

In [10]:
params['template_path'] = r'D:\nvb\GODS_NG\KB-InfoBot\data\templates.j'
nlg = TemplateNLG(params['template_path'])

In [11]:
user_sim = RuleSimulator(movie_dict=movie_kb, act_set=act_set, slot_set=slot_set, 
                         start_set=None, max_turn=max_turn, nlg=nlg, err_prob=err_prob, 
                         db=db_full, dk_prob=(1.-dk_prob), sub_prob=sub_prob, 
                         max_first_turn=max_first_turn)

In [12]:
params['model_name']

'03_06_soft_rl_torch_v3_ent.m'

In [13]:
agent = AgentSimpleRLAllAct(movie_kb, act_set, slot_set, db_inc, 
                                  train=True, _reload=False,
                                  n_hid=params['nhid'], batch=params['batch'], ment=params['ment'],
                                  inputtype=params['input'], pol_start=params['pol_start'], 
                                  lr=params['lr'], upd=params['upd'],
                                  ts=params['ts'], frac=params['frac'], 
                                  max_req=params['max_req'], name=params['model_name'])

In [14]:
agent_eval = AgentSimpleRLAllAct(movie_kb, act_set, slot_set, db_inc, train=False,
            _reload=False, n_hid=params['nhid'],
            batch=params['batch'], ment=params['ment'], inputtype=params['input'],
            pol_start=params['pol_start'],
            lr=params['lr'], upd=params['upd'], tr=params['tr'], ts=params['ts'],
            frac=params['frac'], max_req=params['max_req'], name=params['model_name'])

In [15]:
dialog_manager = DialogManager(agent, user_sim, db_full, db_inc, movie_kb, verbose=False)
dialog_manager_eval = DialogManager(agent_eval, user_sim, db_full, db_inc, movie_kb, verbose=False)

In [16]:
from deep_dialog import dialog_config

In [17]:
import numpy as np
def eval_agent(ite, max_perf, best=False, num_iter=2000, verbose=False):
    print('evaluating....')
    nn = np.sqrt(num_iter)
    if best: 
        agent_eval.load_model(dialog_config.MODEL_PATH + 'best_'+agent_eval._name)
    else: 
        agent_eval.load_model(dialog_config.MODEL_PATH + agent_eval._name)

    all_rewards = np.zeros((num_iter,))
    all_success = np.zeros((num_iter,))
    all_turns = np.zeros((num_iter,))

    for i in range(num_iter):
        current_reward = 0
        current_success = False
        utt = dialog_manager_eval.initialize_episode()
        t = 0
        while(True):
            t += 1
            episode_over, reward, utt, sact = dialog_manager_eval.next_turn()
            current_reward += reward
            if episode_over:
                if reward > 0:
                    current_success = True
                break
        all_rewards[i] = current_reward
        all_success[i] = 1 if current_success else 0
        all_turns[i] = t
    curr_perf = np.mean(all_rewards)
    print("EVAL {}: {} / {} reward {} / {} success rate {} / {} turns".format(ite, \
            curr_perf, np.std(all_rewards)/nn, \
            np.mean(all_success), np.std(all_success)/nn, \
            np.mean(all_turns), np.std(all_turns)/nn))
    if curr_perf > max_perf and not best:
        max_perf = curr_perf
        agent_eval.save_model(dialog_config.MODEL_PATH+'best_'+agent_eval._name)
    if verbose:
        return max_perf, all_rewards, all_success, all_turns    
    return max_perf#, all_rewards, all_success, all_turns

In [18]:
%%time
print("Starting training")
mp = -10.
N = 10_000
EVALF = 100

for i in range(N):
    if i and i % (EVALF * params['batch']) == 0:
        mp = eval_agent(i,mp)
        
    utt = dialog_manager.initialize_episode()
    while(True):
        episode_over, reward, utt, sact = dialog_manager.next_turn()
        if episode_over:
            break
perf = eval_agent('BEST', mp, best=True)


Starting training


C:\ProgramData\Anaconda3\envs\torch_kbinfo\lib\site-packages\torch\optim\lr_scheduler.py:396: UserWarning: To get the last learning rate computed by the scheduler, please use `get_last_lr()`.
  "please use `get_last_lr()`.", UserWarning)


num_updates=1 lr=[0.005] SL update!
Update 1. Avg turns = 5.39 . Avg Reward = -0.69 . Success Rate = 0.29 . Fail Rate = 0.47 . Incomplete Rate = 0.24 . Loss = 10.614
num_updates=2 lr=[0.005] SL update!
Update 2. Avg turns = 3.49 . Avg Reward = -0.47 . Success Rate = 0.31 . Fail Rate = 0.57 . Incomplete Rate = 0.12 . Loss = 7.062
num_updates=3 lr=[0.005] SL update!
Update 3. Avg turns = 4.30 . Avg Reward = -0.54 . Success Rate = 0.31 . Fail Rate = 0.52 . Incomplete Rate = 0.16 . Loss = 9.475
num_updates=4 lr=[0.005] SL update!
Update 4. Avg turns = 4.02 . Avg Reward = -0.38 . Success Rate = 0.36 . Fail Rate = 0.52 . Incomplete Rate = 0.12 . Loss = 8.564
num_updates=5 lr=[0.005] SL update!
Update 5. Avg turns = 4.11 . Avg Reward = -0.34 . Success Rate = 0.38 . Fail Rate = 0.50 . Incomplete Rate = 0.12 . Loss = 8.236
num_updates=6 lr=[0.005] SL update!
Update 6. Avg turns = 3.93 . Avg Reward = -0.29 . Success Rate = 0.39 . Fail Rate = 0.51 . Incomplete Rate = 0.10 . Loss = 7.689
num_updat

ep_cnt=6145 num_updates=48 lr=[0.005] RL update!
Update 48. Avg turns = 3.15 . Avg Reward = 0.04 . Success Rate = 0.50 . Fail Rate = 0.50 . Incomplete Rate = 0.00 . Loss = -0.039
ep_cnt=6273 num_updates=49 lr=[0.005] RL update!
Update 49. Avg turns = 3.16 . Avg Reward = 0.04 . Success Rate = 0.50 . Fail Rate = 0.50 . Incomplete Rate = 0.00 . Loss = -0.030
ep_cnt=6401 num_updates=50 lr=[0.005] RL update!
Update 50. Avg turns = 3.20 . Avg Reward = 0.07 . Success Rate = 0.51 . Fail Rate = 0.49 . Incomplete Rate = 0.00 . Loss = -0.035
ep_cnt=6529 num_updates=51 lr=[0.005] RL update!
Update 51. Avg turns = 3.23 . Avg Reward = 0.11 . Success Rate = 0.53 . Fail Rate = 0.47 . Incomplete Rate = 0.00 . Loss = -0.029
ep_cnt=6657 num_updates=52 lr=[0.005] RL update!
Update 52. Avg turns = 3.24 . Avg Reward = 0.11 . Success Rate = 0.53 . Fail Rate = 0.47 . Incomplete Rate = 0.00 . Loss = -0.048
ep_cnt=6785 num_updates=53 lr=[0.005] RL update!
Update 53. Avg turns = 3.25 . Avg Reward = 0.12 . Succes

FileNotFoundError: [Errno 2] No such file or directory: './data/pretrained/best_03_06_soft_rl_torch_v3_ent.m'

In [25]:
dialog_manager_eval.verbose = False
eval_agent('BEST',mp,best=True, num_iter=5000, verbose=True)
dialog_manager_eval.verbose = False

evaluating....
EVAL BEST: 0.12696000000000005 / 0.018738672089558532 reward 0.5224 / 0.007063968289849551 success rate 3.0 / 0.0 turns


In [26]:
dialog_manager_eval.verbose = True
eval_agent('BEST',mp,best=True, num_iter=1, verbose=True)
dialog_manager_eval.verbose = False

evaluating....
User target =  movie:12 years a slave, actor:tina fey, critic_rating:top rated, genre:fantasy, mpaa_rating:pg-13, director:martin scorcese, release_year:2007
User information =  mpaa_rating:pg-13, director:martin scorcese, release_year:2007 

Turn 0 user action: request 	 inform slots: {'director': 'martin scorcese', 'release_year': '2007', 'mpaa_rating': 'pg-13'}
Utterance: I would like to know a movie whose director is scorcese, mpaa_rating is pg-13 and release_year is 2007. 

Agent updating state:  begin begin
Detected pg-13  update =  1.0
Detected martin scorcese  update =  0.5
Detected 2007  update =  1.0
HDB 8.006273
Turn 1 sys action: request, request slots: {'release_year': 'UNK'}

Turn 1 user action: inform 	 inform slots: {'release_year': '2007'}
Utterance: 2007 release_year 

Agent updating state:  request release_year
Detected 2007  update =  1.0
HDB 7.7876635
Turn 2 sys action: request, request slots: {'genre': 'UNK'}

Turn 2 user action: inform 	 inform slo

In [54]:
agent_new = AgentSimpleRLAllAct(movie_kb, act_set, slot_set, db_inc, 
                                  train=True, _reload=False,
                                  n_hid=params['nhid'], batch=params['batch'], ment=params['ment'],
                                  inputtype=params['input'], pol_start=params['pol_start'], 
                                  lr=params['lr'], upd=params['upd'],
                                  ts=params['ts'], frac=params['frac'], 
                                  max_req=params['max_req'], name=params['model_name'])

In [55]:
dialog_manager_new = DialogManager(agent_new, user_sim, db_full, db_inc, movie_kb, verbose=True)

In [58]:
utt = dialog_manager_new.initialize_episode()
while(True):
    episode_over, reward, utt, sact = dialog_manager_new.next_turn()
    if episode_over:
        break

User target =  movie:for a few dollars more, actor:tina fey, critic_rating:number 1, genre:adult comedy, mpaa_rating:r, director:martin scorcese, release_year:2001
User information =  actor:tina fey, critic_rating:number 1, director:martin scorcese 

Turn 0 user action: request 	 inform slots: {'actor': 'tina fey', 'critic_rating': 'number 1'}
Utterance: Which movie has 0 as critic_rating and tina fey as actor? 

Agent updating state:  begin begin
Detected tina fey  update =  1.0
Turn 1 sys action: request, request slots: {'actor': 'UNK'}

Turn 1 user action: inform 	 inform slots: {'actor': 'tina fey'}
Utterance: It is tina. 

Agent updating state:  request actor
Detected tina fey  update =  0.5
Turn 2 sys action: request, request slots: {'director': 'UNK'}

Turn 2 user action: inform 	 inform slots: {'director': 'martin scorcese'}
Utterance: martin scorcese director 

Agent updating state:  request director
Detected martin scorcese  update =  1.0
Turn 3 sys action: request, request s

In [49]:
def prepare_dialog_managers(params):
    agent = AgentSimpleRLAllAct(movie_kb, act_set, slot_set, db_inc, 
                                  train=True, _reload=False,
                                  n_hid=params['nhid'], batch=params['batch'], ment=params['ment'],
                                  inputtype=params['input'], pol_start=params['pol_start'], 
                                  lr=params['lr'], upd=params['upd'],
                                  ts=params['ts'], frac=params['frac'], 
                                  max_req=params['max_req'], name=params['model_name'])

    agent_eval = AgentSimpleRLAllAct(movie_kb, act_set, slot_set, db_inc, train=False,
                _reload=False, n_hid=params['nhid'],
                batch=params['batch'], ment=params['ment'], inputtype=params['input'],
                pol_start=params['pol_start'],
                lr=params['lr'], upd=params['upd'], tr=params['tr'], ts=params['ts'],
                frac=params['frac'], max_req=params['max_req'], name=params['model_name'])

    dialog_manager = DialogManager(agent, user_sim, db_full, db_inc, movie_kb, verbose=False)
    dialog_manager_eval = DialogManager(agent_eval, user_sim, db_full, db_inc, movie_kb, verbose=False)
    
    return dialog_manager, dialog_manager_eval
    

In [50]:
def train_loop(mp = -10, N = 10_000, EVALF = 100):
    print("Starting training")
    for i in range(N):
        if i and i % (EVALF * params['batch']) == 0:
            mp = eval_agent(i,mp)

        utt = dialog_manager.initialize_episode()
        while(True):
            episode_over, reward, utt, sact = dialog_manager.next_turn()
            if episode_over:
                break
    perf = eval_agent('BEST', mp, best=True, num_iter=5000)
    return perf


In [51]:
def prepare_params(upd, nhid, ment):
    params = {}
    params['max_req'] = 1 # только при SL
    params['frac'] = 0.5 # только при SL
    params['upd'] = upd # C
    params['input'] = 'entropy' 
    params['pol_start'] = 0
    params['nhid'] = nhid
    params['lr'] = 0.005
    params['batch'] = 128
    params['ment'] = ment # RLLoss
    params['ts'] = 0.5 # только при SL
    params['tr'] = 5 # только при SL

    params['model_name'] = f'04_06_soft_rl_torch_v2_{upd}_{nhid}_{ment}.m'
    return params

In [52]:
max_reqs = [1, 2]
fracs = [.3, .4, .5, .6, .7]
upds = [.05, .25, .5, .75, 1, 1.5, 2]
pols = [25, 50]
nhids = [25, 50, 100]
ments = [0, .1, .2, .3]
trs = [3, 5, 7, 9]

In [53]:
from itertools import product
from random import shuffle

In [54]:
params_space = list(product(upds, nhids, ments))

In [55]:
results = {}

In [ ]:
for triple in params_space:
    print()
    print(f"=========={triple}========")
    temp_params = prepare_params(*triple)
    dialog_manager, dialog_manager_eval = prepare_dialog_managers(temp_params)
    best_res = train_loop(mp=-10, N=128 * 200 + 1, EVALF=50)
    results[triple] = best_res
    print()
    


==========(0.05, 25, 0)========
Starting training
ep_cnt=129 num_updates=1 lr=[0.005] RL update!
Update 1. Avg turns = 6.79 . Avg Reward = -0.61 . Success Rate = 0.35 . Fail Rate = 0.21 . Incomplete Rate = 0.44 . Loss = -5.895
ep_cnt=257 num_updates=2 lr=[0.005] RL update!
Update 2. Avg turns = 6.23 . Avg Reward = -0.59 . Success Rate = 0.35 . Fail Rate = 0.29 . Incomplete Rate = 0.37 . Loss = -5.477
ep_cnt=385 num_updates=3 lr=[0.005] RL update!
Update 3. Avg turns = 5.91 . Avg Reward = -0.51 . Success Rate = 0.37 . Fail Rate = 0.31 . Incomplete Rate = 0.32 . Loss = -4.932
ep_cnt=513 num_updates=4 lr=[0.005] RL update!
Update 4. Avg turns = 5.60 . Avg Reward = -0.49 . Success Rate = 0.37 . Fail Rate = 0.35 . Incomplete Rate = 0.28 . Loss = -4.336
ep_cnt=641 num_updates=5 lr=[0.005] RL update!
Update 5. Avg turns = 5.35 . Avg Reward = -0.45 . Success Rate = 0.38 . Fail Rate = 0.37 . Incomplete Rate = 0.25 . Loss = -3.952
ep_cnt=769 num_updates=6 lr=[0.005] RL update!
Update 6. Avg tur

ep_cnt=6017 num_updates=47 lr=[0.005] RL update!
Update 47. Avg turns = 2.00 . Avg Reward = -0.04 . Success Rate = 0.41 . Fail Rate = 0.58 . Incomplete Rate = 0.00 . Loss = 0.123
ep_cnt=6145 num_updates=48 lr=[0.005] RL update!
Update 48. Avg turns = 1.98 . Avg Reward = -0.05 . Success Rate = 0.41 . Fail Rate = 0.59 . Incomplete Rate = 0.00 . Loss = 0.169
ep_cnt=6273 num_updates=49 lr=[0.005] RL update!
Update 49. Avg turns = 2.01 . Avg Reward = -0.07 . Success Rate = 0.41 . Fail Rate = 0.59 . Incomplete Rate = 0.00 . Loss = 0.216
evaluating....
EVAL 6400: -1.8999999999999995 / 9.930136612989092e-18 reward 0.0 / 0.0 success rate 10.0 / 0.0 turns
ep_cnt=6401 num_updates=50 lr=[0.005] RL update!
Update 50. Avg turns = 2.03 . Avg Reward = -0.05 . Success Rate = 0.42 . Fail Rate = 0.58 . Incomplete Rate = 0.00 . Loss = 0.170
ep_cnt=6529 num_updates=51 lr=[0.005] RL update!
Update 51. Avg turns = 2.08 . Avg Reward = -0.05 . Success Rate = 0.42 . Fail Rate = 0.58 . Incomplete Rate = 0.00 . L

ep_cnt=11905 num_updates=93 lr=[0.005] RL update!
Update 93. Avg turns = 2.61 . Avg Reward = -0.03 . Success Rate = 0.45 . Fail Rate = 0.55 . Incomplete Rate = 0.00 . Loss = -0.234
ep_cnt=12033 num_updates=94 lr=[0.005] RL update!
Update 94. Avg turns = 2.64 . Avg Reward = -0.03 . Success Rate = 0.45 . Fail Rate = 0.55 . Incomplete Rate = 0.00 . Loss = -0.261
ep_cnt=12161 num_updates=95 lr=[0.005] RL update!
Update 95. Avg turns = 2.62 . Avg Reward = -0.06 . Success Rate = 0.44 . Fail Rate = 0.56 . Incomplete Rate = 0.00 . Loss = -0.274
ep_cnt=12289 num_updates=96 lr=[0.005] RL update!
Update 96. Avg turns = 2.64 . Avg Reward = -0.01 . Success Rate = 0.46 . Fail Rate = 0.54 . Incomplete Rate = 0.00 . Loss = -0.180
ep_cnt=12417 num_updates=97 lr=[0.005] RL update!
Update 97. Avg turns = 2.63 . Avg Reward = -0.02 . Success Rate = 0.45 . Fail Rate = 0.54 . Incomplete Rate = 0.00 . Loss = -0.128
ep_cnt=12545 num_updates=98 lr=[0.005] RL update!
Update 98. Avg turns = 2.62 . Avg Reward = -0

ep_cnt=17665 num_updates=138 lr=[0.005] RL update!
Update 138. Avg turns = 2.01 . Avg Reward = -0.01 . Success Rate = 0.43 . Fail Rate = 0.57 . Incomplete Rate = 0.00 . Loss = 0.078
ep_cnt=17793 num_updates=139 lr=[0.005] RL update!
Update 139. Avg turns = 2.02 . Avg Reward = -0.04 . Success Rate = 0.42 . Fail Rate = 0.58 . Incomplete Rate = 0.00 . Loss = 0.039
ep_cnt=17921 num_updates=140 lr=[0.005] RL update!
Update 140. Avg turns = 2.04 . Avg Reward = -0.04 . Success Rate = 0.42 . Fail Rate = 0.58 . Incomplete Rate = 0.00 . Loss = -0.027
ep_cnt=18049 num_updates=141 lr=[0.005] RL update!
Update 141. Avg turns = 2.05 . Avg Reward = -0.07 . Success Rate = 0.41 . Fail Rate = 0.59 . Incomplete Rate = 0.00 . Loss = -0.029
ep_cnt=18177 num_updates=142 lr=[0.005] RL update!
Update 142. Avg turns = 2.08 . Avg Reward = -0.06 . Success Rate = 0.42 . Fail Rate = 0.58 . Incomplete Rate = 0.00 . Loss = -0.043
ep_cnt=18305 num_updates=143 lr=[0.005] RL update!
Update 143. Avg turns = 2.09 . Avg R

ep_cnt=23425 num_updates=183 lr=[0.005] RL update!
Update 183. Avg turns = 2.10 . Avg Reward = -0.02 . Success Rate = 0.43 . Fail Rate = 0.57 . Incomplete Rate = 0.00 . Loss = -0.021
ep_cnt=23553 num_updates=184 lr=[0.005] RL update!
Update 184. Avg turns = 2.10 . Avg Reward = -0.02 . Success Rate = 0.43 . Fail Rate = 0.57 . Incomplete Rate = 0.00 . Loss = 0.010
ep_cnt=23681 num_updates=185 lr=[0.005] RL update!
Update 185. Avg turns = 2.15 . Avg Reward = 0.02 . Success Rate = 0.45 . Fail Rate = 0.55 . Incomplete Rate = 0.00 . Loss = 0.043
ep_cnt=23809 num_updates=186 lr=[0.005] RL update!
Update 186. Avg turns = 2.13 . Avg Reward = 0.04 . Success Rate = 0.45 . Fail Rate = 0.55 . Incomplete Rate = 0.00 . Loss = 0.027
ep_cnt=23937 num_updates=187 lr=[0.005] RL update!
Update 187. Avg turns = 2.15 . Avg Reward = 0.04 . Success Rate = 0.46 . Fail Rate = 0.54 . Incomplete Rate = 0.00 . Loss = 0.015
ep_cnt=24065 num_updates=188 lr=[0.005] RL update!
Update 188. Avg turns = 2.19 . Avg Reward

...

ep_cnt=2433 num_updates=19 lr=[0.005] RL update!
Update 19. Avg turns = 3.04 . Avg Reward = -0.06 . Success Rate = 0.46 . Fail Rate = 0.52 . Incomplete Rate = 0.02 . Loss = -4.183
ep_cnt=2561 num_updates=20 lr=[0.005] RL update!
Update 20. Avg turns = 3.12 . Avg Reward = -0.05 . Success Rate = 0.46 . Fail Rate = 0.51 . Incomplete Rate = 0.03 . Loss = -4.249
ep_cnt=2689 num_updates=21 lr=[0.005] RL update!
Update 21. Avg turns = 3.22 . Avg Reward = -0.08 . Success Rate = 0.45 . Fail Rate = 0.52 . Incomplete Rate = 0.03 . Loss = -4.248
ep_cnt=2817 num_updates=22 lr=[0.005] RL update!
Update 22. Avg turns = 3.31 . Avg Reward = -0.09 . Success Rate = 0.45 . Fail Rate = 0.52 . Incomplete Rate = 0.03 . Loss = -4.354
ep_cnt=2945 num_updates=23 lr=[0.005] RL update!
Update 23. Avg turns = 3.39 . Avg Reward = -0.04 . Success Rate = 0.47 . Fail Rate = 0.49 . Incomplete Rate = 0.04 . Loss = -4.517
ep_cnt=3073 num_updates=24 lr=[0.005] RL update!
Update 24. Avg turns = 3.48 . Avg Reward = -0.09 . 

ep_cnt=8193 num_updates=64 lr=[0.005] RL update!
Update 64. Avg turns = 3.73 . Avg Reward = -0.02 . Success Rate = 0.49 . Fail Rate = 0.49 . Incomplete Rate = 0.02 . Loss = -4.192
ep_cnt=8321 num_updates=65 lr=[0.005] RL update!
Update 65. Avg turns = 3.77 . Avg Reward = -0.02 . Success Rate = 0.50 . Fail Rate = 0.48 . Incomplete Rate = 0.02 . Loss = -4.218
ep_cnt=8449 num_updates=66 lr=[0.005] RL update!
Update 66. Avg turns = 3.76 . Avg Reward = -0.03 . Success Rate = 0.49 . Fail Rate = 0.49 . Incomplete Rate = 0.02 . Loss = -4.171
ep_cnt=8577 num_updates=67 lr=[0.005] RL update!
Update 67. Avg turns = 3.75 . Avg Reward = -0.06 . Success Rate = 0.48 . Fail Rate = 0.50 . Incomplete Rate = 0.01 . Loss = -4.233
ep_cnt=8705 num_updates=68 lr=[0.005] RL update!
Update 68. Avg turns = 3.80 . Avg Reward = -0.06 . Success Rate = 0.49 . Fail Rate = 0.50 . Incomplete Rate = 0.02 . Loss = -4.264
ep_cnt=8833 num_updates=69 lr=[0.005] RL update!
Update 69. Avg turns = 3.87 . Avg Reward = -0.07 . 

ep_cnt=13953 num_updates=109 lr=[0.005] RL update!
Update 109. Avg turns = 3.92 . Avg Reward = -0.10 . Success Rate = 0.47 . Fail Rate = 0.51 . Incomplete Rate = 0.02 . Loss = -4.521
ep_cnt=14081 num_updates=110 lr=[0.005] RL update!
Update 110. Avg turns = 3.97 . Avg Reward = -0.12 . Success Rate = 0.47 . Fail Rate = 0.51 . Incomplete Rate = 0.02 . Loss = -4.508
ep_cnt=14209 num_updates=111 lr=[0.005] RL update!
Update 111. Avg turns = 3.98 . Avg Reward = -0.11 . Success Rate = 0.47 . Fail Rate = 0.51 . Incomplete Rate = 0.02 . Loss = -4.516
ep_cnt=14337 num_updates=112 lr=[0.005] RL update!
Update 112. Avg turns = 3.98 . Avg Reward = -0.09 . Success Rate = 0.48 . Fail Rate = 0.51 . Incomplete Rate = 0.01 . Loss = -4.532
ep_cnt=14465 num_updates=113 lr=[0.005] RL update!
Update 113. Avg turns = 3.96 . Avg Reward = -0.08 . Success Rate = 0.48 . Fail Rate = 0.50 . Incomplete Rate = 0.02 . Loss = -4.509
ep_cnt=14593 num_updates=114 lr=[0.005] RL update!
Update 114. Avg turns = 3.93 . Avg

ep_cnt=19713 num_updates=154 lr=[0.005] RL update!
Update 154. Avg turns = 3.78 . Avg Reward = -0.05 . Success Rate = 0.48 . Fail Rate = 0.51 . Incomplete Rate = 0.01 . Loss = -4.291
ep_cnt=19841 num_updates=155 lr=[0.005] RL update!
Update 155. Avg turns = 3.75 . Avg Reward = -0.02 . Success Rate = 0.49 . Fail Rate = 0.50 . Incomplete Rate = 0.01 . Loss = -4.308
ep_cnt=19969 num_updates=156 lr=[0.005] RL update!
Update 156. Avg turns = 3.69 . Avg Reward = -0.01 . Success Rate = 0.50 . Fail Rate = 0.50 . Incomplete Rate = 0.00 . Loss = -4.294
ep_cnt=20097 num_updates=157 lr=[0.005] RL update!
Update 157. Avg turns = 3.75 . Avg Reward = -0.04 . Success Rate = 0.49 . Fail Rate = 0.51 . Incomplete Rate = 0.01 . Loss = -4.236
ep_cnt=20225 num_updates=158 lr=[0.005] RL update!
Update 158. Avg turns = 3.75 . Avg Reward = -0.06 . Success Rate = 0.48 . Fail Rate = 0.52 . Incomplete Rate = 0.01 . Loss = -4.170
ep_cnt=20353 num_updates=159 lr=[0.005] RL update!
Update 159. Avg turns = 3.72 . Avg

ep_cnt=25473 num_updates=199 lr=[0.005] RL update!
Update 199. Avg turns = 3.70 . Avg Reward = -0.07 . Success Rate = 0.48 . Fail Rate = 0.52 . Incomplete Rate = 0.01 . Loss = -4.222
evaluating....
EVAL 25600: -1.8999999999999995 / 9.930136612989092e-18 reward 0.0 / 0.0 success rate 10.0 / 0.0 turns
ep_cnt=25601 num_updates=200 lr=[0.005] RL update!
Update 200. Avg turns = 3.69 . Avg Reward = -0.06 . Success Rate = 0.48 . Fail Rate = 0.51 . Incomplete Rate = 0.01 . Loss = -4.097
evaluating....


In [46]:
prepare_params(*x[0])

{'max_req': 1,
 'frac': 0.5,
 'upd': 0.05,
 'input': 'entropy',
 'pol_start': 0,
 'nhid': 25,
 'lr': 0.005,
 'batch': 128,
 'ment': 0,
 'ts': 0.5,
 'tr': 5,
 'model_name': '04_06_soft_rl_torch_v2_0.05_25_0.m'}

In [41]:
#v5
dialog_manager_eval.verbose = True
perf = eval_agent('BEST',mp,best=True, num_iter=5000)

evaluating....
User target =  movie:rocky, actor:ryan reynolds, critic_rating:4.5/5, genre:adventure, mpaa_rating:r, director:quentin tarantino, release_year:2013
User information =  genre:adventure, mpaa_rating:r, release_year:2013 

Turn 0 user action: request 	 inform slots: {'mpaa_rating': 'r'}
Utterance: Can you please tell me which movie has r as mpaa_rating? 

Agent updating state:  begin begin
Detected r  update =  1.0
Turn 1 sys action: request, request slots: {'genre': 'UNK'}

Turn 1 user action: inform 	 inform slots: {'genre': 'adventure'}
Utterance: adventure genre 

Agent updating state:  request genre
Detected adventure  update =  1.0
Turn 2 sys action: request, request slots: {'release_year': 'UNK'}

Turn 2 user action: inform 	 inform slots: {'release_year': '2013'}
Utterance: 2013 release_year 

Agent updating state:  request release_year
Detected 2013  update =  1.0
Turn 3 sys action: inform, request slots: {}

Agent Results:
rocky	ryan reynolds	4.5/5	adventure	r	que

Turn 3 sys action: inform, request slots: {}

Agent Results:
12 angry men	ryan reynolds	UNK	drama	r	martin scorcese	2008
infernal affairs	ryan reynolds	UNK	drama	r	quentin tarantino	UNK
amadeus	ryan reynolds	UNK	drama	pg-13	christopher nolan	2009
wild strawberries	ryan reynolds	top	drama	pg-13	zack snyder	2011
indiana jones and the last crusade	tina fey	84 percent	drama	pg-13	quentin tarantino	UNK
User target =  movie:fight club, actor:ryan reynolds, critic_rating:number 1, genre:animated, mpaa_rating:pg-13, director:christopher nolan, release_year:2014
User information =  critic_rating:number 1, genre:animated, release_year:2014 

Turn 0 user action: request 	 inform slots: {'genre': 'animated', 'release_year': '2014', 'critic_rating': 'number 1'}
Utterance: Can you please tell me a movie whose genre is animated, release_year is 2014 and critic_rating is 0? 

Agent updating state:  begin begin
Detected animated  update =  1.0
Detected 2014  update =  1.0
Turn 1 sys action: request, re

User target =  movie:jaws, actor:ryan reynolds, critic_rating:26%, genre:action, mpaa_rating:r, director:christopher nolan, release_year:2011
User information =  genre:action, director:christopher nolan, release_year:2011 

Turn 0 user action: request 	 inform slots: {'director': 'christopher nolan', 'genre': 'action', 'release_year': '2011'}
Utterance: I would like to know a movie whose director is christopher nolan, genre is action and release_year is 2011. 

Agent updating state:  begin begin
Detected action  update =  1.0
Detected christopher nolan  update =  1.0
Detected 2011  update =  1.0
Turn 1 sys action: request, request slots: {'genre': 'UNK'}

Turn 1 user action: inform 	 inform slots: {'genre': 'action'}
Utterance: action genre 

Agent updating state:  request genre
Detected action  update =  1.0
Turn 2 sys action: request, request slots: {'release_year': 'UNK'}

Turn 2 user action: inform 	 inform slots: {'release_year': '2011'}
Utterance: I think it is 2010. 

Agent upda

Removing slot release_year from db!
Turn 3 sys action: inform, request slots: {}

Agent Results:
my neighbor totoro	tina fey	top rated	action	pg	zack snyder	2009
casino	tina fey	6	action	pg	quentin tarantino	2003
schindler's list	tina fey	top rated	action	pg	zack snyder	2015
interstellar	tina fey	8%	action	UNK	zack snyder	UNK
london has fallen	tina fey	5	action	UNK	quentin tarantino	2010
User target =  movie:the gold rush, actor:ryan reynolds, critic_rating:84 percent, genre:thriller, mpaa_rating:pg, director:martin scorcese, release_year:2001
User information =  actor:ryan reynolds, critic_rating:84 percent, director:martin scorcese 

Turn 0 user action: request 	 inform slots: {'actor': 'ryan reynolds', 'critic_rating': '84 percent'}
Utterance: Which movie has 84 percent as critic_rating and ryan reynolds as actor? 

Agent updating state:  begin begin
Detected ryan reynolds  update =  1.0
Detected 84 percent  update =  1.0
Turn 1 sys action: request, request slots: {'genre': 'UNK'}




Turn 2 user action: inform 	 inform slots: {'release_year': None}
Utterance: I cannot remember 

Agent updating state:  request release_year
Removing slot release_year from db!
Turn 3 sys action: inform, request slots: {}

Agent Results:
there will be blood	tina fey	good	sci-fi	pg-13	martin scorcese	2002
triple 9	tina fey	good	romantic comedy	UNK	martin scorcese	2003
das boot	ryan reynolds	good	animated	UNK	martin scorcese	2004
the martian	ryan reynolds	good	sci-fi	pg-13	UNK	2010
batman begins	ryan reynolds	good	horror	pg	martin scorcese	2005
User target =  movie:the lives of others, actor:tina fey, critic_rating:5, genre:romantic comedy, mpaa_rating:pg-13, director:quentin tarantino, release_year:2001
User information =  actor:tina fey, genre:romantic comedy, mpaa_rating:pg-13 

Turn 0 user action: request 	 inform slots: {'mpaa_rating': 'pg-13', 'actor': 'tina fey'}
Utterance: I would like to know a movie whose mpaa_rating is pg-13 and actor is tina. 

Agent updating state:  begin b

...

Detected ryan reynolds  update =  0.5
Detected pg-13  update =  1.0
Detected 2004  update =  1.0
Turn 1 sys action: request, request slots: {'genre': 'UNK'}

Turn 1 user action: inform 	 inform slots: {'genre': None}
Utterance: I cannot remember 

Agent updating state:  request genre
Removing slot genre from db!
Turn 2 sys action: request, request slots: {'release_year': 'UNK'}

Turn 2 user action: inform 	 inform slots: {'release_year': '2004'}
Utterance: 2004 release_year 

Agent updating state:  request release_year
Detected 2004  update =  1.0
Turn 3 sys action: inform, request slots: {}

Agent Results:
the grapes of wrath	ryan reynolds	top	UNK	pg-13	UNK	2004
psycho	tina fey	good	sci-fi	pg-13	quentin tarantino	2004
the grand budapest hotel	ryan reynolds	4.5/5	UNK	UNK	quentin tarantino	2004
das boot	ryan reynolds	good	animated	UNK	martin scorcese	2004
inception	UNK	UNK	comedy	UNK	christopher nolan	2004
User target =  movie:princess mononoke, actor:ryan reynolds, critic_rating:4.5/5,

Detected thriller science fiction  update =  0.3333333333333333
Detected thriller  update =  1.0
Turn 2 sys action: request, request slots: {'release_year': 'UNK'}

Turn 2 user action: inform 	 inform slots: {'release_year': None}
Utterance: I dont know 

Agent updating state:  request release_year
Removing slot release_year from db!
Turn 3 sys action: inform, request slots: {}

Agent Results:
mr. smith goes to washington	tina fey	good	thriller	r	zack snyder	2008
the pianist	tina fey	8%	thriller	pg	zack snyder	2015
the intouchables	UNK	84 percent	thriller	UNK	zack snyder	2013
10 cloverfield lane	UNK	8%	thriller	pg-13	zack snyder	2015
the green mile	tina fey	26%	thriller science fiction	r	UNK	2013
User target =  movie:8Ѕ, actor:tina fey, critic_rating:number 1, genre:animated, mpaa_rating:pg-13, director:zack snyder, release_year:2003
User information =  actor:tina fey, mpaa_rating:pg-13, release_year:2003 

Turn 0 user action: request 	 inform slots: {'release_year': '2003', 'actor': '

Utterance: 2007 release_year 

Agent updating state:  request release_year
Detected 2007  update =  1.0
Turn 3 sys action: inform, request slots: {}

Agent Results:
full metal jacket	tina fey	top	adventure	r	christopher nolan	2007
the third man	tina fey	4.5/5	adventure	pg	christopher nolan	2008
the elephant man	ryan reynolds	UNK	adventure	pg-13	martin scorcese	2008
a fistful of dollars	tina fey	top rated	UNK	UNK	christopher nolan	2007
vertigo	tina fey	5	adventure	r	christopher nolan	2015
User target =  movie:the help, actor:ryan reynolds, critic_rating:4.5/5, genre:animated, mpaa_rating:r, director:zack snyder, release_year:2008
User information =  actor:ryan reynolds, director:zack snyder, release_year:2008 

Turn 0 user action: request 	 inform slots: {'director': 'zack snyder', 'release_year': '2008', 'actor': 'ryan reynolds'}
Utterance: I am looking for a movie with actor ryan reynolds, release_year 2008 and director snyder. 

Agent updating state:  begin begin
Detected ryan reynol

Detected number 1  update =  1.0
Detected pg  update =  1.0
Detected 2004  update =  1.0
Turn 1 sys action: request, request slots: {'genre': 'UNK'}

Turn 1 user action: inform 	 inform slots: {'genre': None}
Utterance: I am not sure 

Agent updating state:  request genre
Removing slot genre from db!
Turn 2 sys action: request, request slots: {'release_year': 'UNK'}

Turn 2 user action: inform 	 inform slots: {'release_year': '2004'}
Utterance: 2004 

Agent updating state:  request release_year
Detected 2004  update =  1.0
Turn 3 sys action: inform, request slots: {}

Agent Results:
brothers grimsby	tina fey	number 1	animated	pg	quentin tarantino	2004
scarface	tina fey	UNK	sci-fi	pg	christopher nolan	2004
no country for old men	ryan reynolds	UNK	fantasy	pg	zack snyder	2004
citizen kane	tina fey	84 percent	fantasy	pg	quentin tarantino	2004
gone girl	tina fey	top rated	comedy	pg	UNK	2004
User target =  movie:8Ѕ, actor:tina fey, critic_rating:number 1, genre:animated, mpaa_rating:pg-13, d

Turn 1 user action: inform 	 inform slots: {'genre': None}
Utterance: I cannot remember 

Agent updating state:  request genre
Removing slot genre from db!
Turn 2 sys action: request, request slots: {'release_year': 'UNK'}

Turn 2 user action: inform 	 inform slots: {'release_year': None}
Utterance: I am not sure 

Agent updating state:  request release_year
Removing slot release_year from db!
Turn 3 sys action: inform, request slots: {}

Agent Results:
schindler's list	tina fey	top rated	action	pg	zack snyder	2015
room	tina fey	top rated	thriller	pg-13	christopher nolan	2008
barry lyndon	ryan reynolds	top rated	sci-fi	pg	martin scorcese	2009
saving private ryan	ryan reynolds	top rated	thriller	pg	christopher nolan	2010
spirited away	tina fey	top rated	romance	r	quentin tarantino	UNK
User target =  movie:donnie darko, actor:tina fey, critic_rating:top rated, genre:romance, mpaa_rating:r, director:martin scorcese, release_year:2004
User information =  genre:romance, mpaa_rating:r, relea

In [35]:
#v4
perf = eval_agent('BEST',mp,best=True, num_iter=5000)

evaluating....
EVAL BEST: 0.17838 / 0.018765343458620735 reward 0.592 / 0.0069503381212715105 success rate 4.637 / 0.006800455867072441 turns


In [28]:
import torch

In [40]:
agent.rl_scheduler.get_lr()

0.005

In [49]:
torch.ones((4,3)).type(torch.int8)

tensor([[1, 1, 1],
        [1, 1, 1],
        [1, 1, 1],
        [1, 1, 1]], dtype=torch.int8)

In [21]:
import torch
a = torch.rand(5)
a

tensor([0.5549, 0.8657, 0.6097, 0.4026, 0.3731])

In [23]:
torch.argmax(a).item()

1

In [72]:
N = 200
dialog_manager = DialogManager(agent, user_sim, db_full, db_inc, movie_kb, verbose=False)

In [139]:
%%time
for i in range(1):
    utt = dialog_manager.initialize_episode()
    while(True):
        episode_over, reward, utt, sact = dialog_manager.next_turn()
        if episode_over:
            break

generating frmo template
probs= [0.09390948 0.25737811 0.30741048 0.14465148 0.04863243 0.06973738
 0.07828064]
Network action 0
generating frmo nlg
sent= the actor is fey.
probs= [0.06584557 0.26594798 0.4236722  0.1127263  0.02757506 0.04688806
 0.05734483]
Network action 3
generating frmo nlg
sent= i cannot remember
probs= [0.04812919 0.22629019 0.52158225 0.09787374 0.02216652 0.03388566
 0.05007245]
Network action 1
generating frmo nlg
sent= i cannot remember
probs= [0.03873961 0.18257008 0.60211719 0.07964679 0.01711302 0.03606868
 0.04374461]
Network action 2
generating frmo nlg
sent= i cannot remember
probs= [0.04680305 0.18303522 0.57652636 0.0773532  0.01833679 0.0498473
 0.04809808]
Network action 2
generating frmo nlg
sent= i cannot remember
probs= [0.04477153 0.16994732 0.58846698 0.07830012 0.01852861 0.05198256
 0.04800288]
Network action 2
generating frmo nlg
sent= i cannot remember
probs= [0.04149489 0.15979321 0.60371371 0.07847681 0.01866978 0.05027617
 0.04757542]
N

In [47]:
i, t, a, r = agent._get_minibatch(128)

In [50]:
a.shape

(127, 10, 7)

In [43]:
len(agent.input_pool)

127

In [26]:
agent.episode_count, agent.batch_size

(4, 128)

In [38]:
agent.batch

AttributeError: 'AgentSimpleRLAllAct' object has no attribute 'batch'

In [10]:
import torch
import torch.nn as nn
import torch.nn.functional as F

In [168]:
class RLPolicy(nn.Module):
    def __init__(self, in_size, out_size, n_hid=10, seq_len=10, learning_rate_sl=0.005, \
            learning_rate_rl=0.005, batch_size=32, ment=0.1):
        super(RLPolicy, self).__init__()
        self.in_size = in_size 
        self.out_size = out_size 
        self.batch_size = batch_size
        self.seq_len = seq_len
        self.learning_rate = learning_rate_rl
        self.n_hid = n_hid
         
        self.gru = nn.GRU(input_size=in_size, hidden_size=n_hid, num_layers=1, batch_first=True)      
        self.fc1 = nn.Linear(in_features=self.n_hid, out_features=out_size)
        
    def forward(self, input_var, turn_mask, act_mask, reward_var, pol_in):
        output, pol_out = self.gru(input_var, pol_in)
        # output.shape = (batch_size x seq_len x n_hid)
        # pol_out.shape = (batch_size x 1 x n_hid)
        output = output.reshape((self.batch_size * self.seq_len, n_hid))
        
        probs = F.softmax(self.fc1(output), dim=1)
        # probs.shape = (batch_size x seq_len, out_size)
        out_probs = probs.view((self.batch_size, self.seq_len, out_size))
        log_probs = torch.log(out_probs)
        # log_probs.shape = (batch_size, seq_len, out_size)
        
        # act_probs [batch x max_turn] act_probs[b][i] - значение логарифма вероятности выбранного на шаге i действия
        act_probs = (log_probs * act_mask).sum(dim=2) # B x H
        
        # * turn_mask - маска для сделанных действий в этом эпизоде
        # ep_probs[b] - сумма логарифмов вероятностей действий, сделанных в эпизоде b
        ep_probs = (act_probs * turn_mask).sum(dim=1) # B
        
        # энтропия для каждого эпизода
        H_probs = -torch.sum(torch.sum(out_probs * log_probs, dim=2), dim=1) # B
        
        # reward_var - награды за эпизоды
        loss = 0. - torch.mean(ep_probs * reward_var + ment * H_probs)
        
        # sl
        # чем меньше уверенность в действиях, тем больше лосс
        sl_loss = 0. - torch.mean(ep_probs)
        
        return out_probs, pol_out, loss, sl_loss
    

In [175]:
def RLLoss(out_probs, turn_mask, act_mask, reward_var):
    log_probs = torch.log(out_probs)
    # log_probs.shape = (batch_size, seq_len, out_size)

    # act_probs [batch x max_turn] act_probs[b][i] - значение логарифма вероятности выбранного на шаге i действия
    act_probs = (log_probs * act_mask).sum(dim=2) # B x H

    # * turn_mask - маска для сделанных действий в этом эпизоде
    # ep_probs[b] - сумма логарифмов вероятностей действий, сделанных в эпизоде b
    ep_probs = (act_probs * turn_mask).sum(dim=1) # B

    # энтропия для каждого эпизода
    H_probs = -torch.sum(torch.sum(out_probs * log_probs, dim=2), dim=1) # B

    # reward_var - награды за эпизоды
    loss = 0. - torch.mean(ep_probs * reward_var + ment * H_probs)
    
    return loss

def SLLoss(out_probs, turn_mask, act_mask):
    log_probs = torch.log(out_probs)
    # log_probs.shape = (batch_size, seq_len, out_size)

    # act_probs [batch x max_turn] act_probs[b][i] - значение логарифма вероятности выбранного на шаге i действия
    act_probs = (log_probs * act_mask).sum(dim=2) # B x H

    # * turn_mask - маска для сделанных действий в этом эпизоде
    # ep_probs[b] - сумма логарифмов вероятностей действий, сделанных в эпизоде b
    ep_probs = (act_probs * turn_mask).sum(dim=1) # B

    sl_loss = 0. - torch.mean(ep_probs)
    
    return sl_loss

In [170]:
in_size = 24
out_size = 7
n_hid = 5
lr = .01
batch = 2
ment = 0
seq_len = 10

pol = RLPolicy(in_size=in_size, out_size=out_size, n_hid=n_hid, seq_len=seq_len,
               learning_rate_sl=lr, learning_rate_rl=lr, batch_size=batch, ment=ment)

In [187]:
torch.zeros((5, 2))

tensor([[0., 0.],
        [0., 0.],
        [0., 0.],
        [0., 0.],
        [0., 0.]])

In [185]:
torch.optim.RMSprop

torch.optim.rmsprop.RMSprop

In [183]:
torch.log

<function _VariableFunctions.log>

In [171]:
op, po, loss, slL = pol(i, t, a, r, pi)

In [182]:
SLLoss(op, t, a)

tensor(4.2021, grad_fn=<RsubBackward1>)

In [179]:
x = torch.rand((100, 5), requires_grad=True)
y = 2 * x + 1

In [180]:
loss = nn.MSELoss()

In [181]:
loss(x, y)

tensor(2.4244, grad_fn=<MeanBackward0>)

In [172]:
loss, slL

(tensor(-4.5803, grad_fn=<RsubBackward1>),
 tensor(4.2021, grad_fn=<RsubBackward1>))

In [140]:
act_probs = (op * a).sum(dim=2)
act_probs

tensor([[0.1466, 0.0934, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000],
        [0.1411, 0.1029, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000]], grad_fn=<SumBackward1>)

In [141]:
act_probs * t

tensor([[0.1466, 0.0934, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000],
        [0.1411, 0.1029, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
         0.0000]], grad_fn=<MulBackward0>)

In [79]:
import numpy as np
i = torch.rand((2, 10, 24))
t = torch.Tensor([[1, 1, 0, 0, 0, 0, 0, 0, 0, 0],
       [1, 1, 0, 0, 0, 0, 0, 0, 0, 0]])
a = torch.Tensor([[[0, 1, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 1],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0]],

       [[0, 1, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 1],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0],
        [0, 0, 0, 0, 0, 0, 0]]])

r = torch.Tensor([-1.09, -1.09])

pi = torch.zeros((1, 2, n_hid))

In [95]:
ps = np.random.rand(100, 2)
r = np.random.uniform(-1, 1, 100)
ps[:, 1] = 1 - ps[:, 0]

In [96]:
f = np.log(ps).sum(axis=1) * r
print(max(f), ps[np.argmax(f), :], r[np.argmax(f)])
print(min(f), ps[np.argmin(f), :], r[np.argmin(f)])

3.3504600931047235 [0.98609682 0.01390318] -0.781058915944641
-3.3729302781048247 [0.98004489 0.01995511] 0.8572862698574326


In [91]:
ps1 = np.array([.5, .5])
np.log(ps1).sum() * (-0.95)

1.316979643063896

In [69]:
r = [.2, 0.6]

In [70]:
f = (ps * r).sum(axis=1)
min(f), max(f)

(0.20159032127197368, 0.5935811441340709)